In [1]:
import math
import random
import itertools
import matplotlib.pyplot as plt
from tqdm import tqdm

import numpy as np
import numba
import numpy.random
from collections import deque

import tensorflow as tf
from tensorflow.keras import Model, Sequential
from tensorflow.keras.layers import Dense, Embedding, Reshape
from tensorflow.keras.optimizers import Adam

In [9]:
class GridWorld:
    def __init__(self, taille=[4, 4], position_start=[0, 1], good_end_position=[3, 2], bad_end_position=[0, 3]):
        self.current_state = position_start  # État actuel (ligne, colonne)
        self.states = [[x, y] for x in range(taille[0]) for y in range(taille[1])]
        self.end_good_state = good_end_position  # État final (ligne, colonne)
        self.end_bad_state = bad_end_position
        self.grid_size = taille  # Taille de la grille (lignes, colonnes)
        self.stateSpace = {}
        self.matchStates()
        self.currentIntState = self.getStateInt(self.current_state)
        self.num_actions = 4  # Nombre total d'actions possibles (haut, bas, gauche, droite)
        self.reward = 0  # Récompense actuelle
        self.done = False  # Indique si la partie est terminée
        #self.generate_grid()
        self.actions = [0, 1, 2, 3]
        self.rewards = [0, 1, 3]
        self.actionSpace = {0: -self.grid_size[0], 1: self.grid_size[0],
                            2: -1, 3: 1}

    def state_description(self):
        return np.array([self.currentIntState / (len(self.states) - 1) * 2.0 - 1.0])

    def state_dim(self):
        return len(self.state_description())

    def reset(self):
        self.done = False
        self.current_state = [np.random.randint(0, self.grid_size[0] - 1), np.random.randint(0, self.grid_size[1] - 1)]
        self.currentIntState = self.getStateInt(self.current_state)
        self.reward = 0

    def matchStates(self):
        i = 0
        for s in self.states:
            self.stateSpace[str(s)] = i
            i = i + 1

    def getStateInt(self, st):
        return self.stateSpace[str(st)]

    def getStateCouple(self, st):
        n_state = {i for i in self.stateSpace if self.stateSpace[i] == st}
        return list(n_state)

    def step(self, action):
        if action == 0:
            if self.current_state[0] == 0:
                self.current_state[0] = self.grid_size[0] - 1
                self.currentIntState = self.getStateInt(self.current_state)
                self.reward = 0  # Pas de récompense pour traverser le mur
                #self.generate_grid()
                self.endgame()
            else:
                self.current_state[0] = self.current_state[0] - 1
                self.currentIntState = self.getStateInt(self.current_state)
                self.reward = 0  # Pas de récompense pour avancer
                #self.generate_grid()
                self.endgame()

        elif action == 1:
            if self.current_state[0] == self.grid_size[0] - 1:
                self.current_state[0] = 0
                self.currentIntState = self.getStateInt(self.current_state)
                self.reward = 0  # Pas de récompense pour avancer
                #self.generate_grid()
                self.endgame()
            else:
                self.current_state[0] = self.current_state[0] + 1
                self.currentIntState = self.getStateInt(self.current_state)
                self.reward = 0  # Pas de récompense pour avancer
                #self.generate_grid()
                self.endgame()

        elif action == 2:
            if self.current_state[1] == 0:
                self.current_state[1] = self.grid_size[1] - 1
                self.currentIntState = self.getStateInt(self.current_state)
                self.reward = 0  # Pas de récompense pour avancer
                #self.generate_grid()
                self.endgame()
            else:
                self.current_state[1] = self.current_state[1] - 1
                self.currentIntState = self.getStateInt(self.current_state)
                self.reward = 0  # Pas de récompense pour avancer
                #self.generate_grid()
                self.endgame()

        elif action == 3:
            if self.current_state[1] == self.grid_size[1] - 1:
                self.current_state[1] = 0
                self.currentIntState = self.getStateInt(self.current_state)
                # print(self.current_state)
                self.reward = 0  # Pas de récompense pour avancer
                #self.generate_grid()
                self.endgame()
            else:
                self.current_state[1] = self.current_state[1] + 1
                self.currentIntState = self.getStateInt(self.current_state)
                self.reward = 0  # Pas de récompense pour avancer
                #self.generate_grid()
                self.endgame()
                # Si l'on atteint l'état final, la partie est terminée
        return self.currentIntState, self.reward, self.done

    def endgame(self):
        if self.current_state == self.end_good_state:
            self.reward = 10  # Récompense de 10 pour atteindre l'état final
            self.done = True
            print("Une bonne récompense")
        elif self.current_state == self.end_bad_state:
            self.reward = -10
            self.done = True
            print("Une mauvaise récompense")

    def generate_grid(self):
        grid = []
        for i in range(self.grid_size[0]):
            grid.append([])
            for j in range(self.grid_size[1]):
                grid[i].append("_")
        grid[self.current_state[0]][self.current_state[1]] = "X"
        for i in grid:
            print(i)
        print("\n")

In [3]:
def clone(env):
    new_env = GridWorld()
    new_env.currentIntState = env.currentIntState
    new_env.grid_size = env.grid_size
    new_env.actions = env.actions.copy()
    new_env.done = env.done
    new_env.reward = env.reward
    new_env.current_state = env.current_state
    return new_env


In [8]:
def monte_carlo_random_rollout_and_choose_action(env,simulation_count_per_action: int = 50) -> int:
    best_action = None
    best_action_average_score = None
    for a in np.array(env.actions):
        action_score = 0.0
        for _ in range(simulation_count_per_action):
            cloned_env = clone(env)
            cloned_env.step(a)

            while not cloned_env.done:
                cloned_env.step(np.random.choice(np.array(cloned_env.actions)))

            action_score += cloned_env.reward
        average_action_score = action_score / simulation_count_per_action

        if best_action_average_score is None or best_action_average_score < average_action_score:
            best_action = a
            best_action_average_score = average_action_score
    return best_action


def run_ttt_n_games_and_return_mean_score(games_count: int) -> float:
    rewards_per_episode = []
    env = GridWorld()
    total = 0.0
    for _ in tqdm(range(games_count)):
        env.reset()

        while not env.done:
            chosen_a = monte_carlo_random_rollout_and_choose_action(env)
            env.step(chosen_a)

        rewards_per_episode.append(env.reward)
        total += env.reward
    return (total / games_count), rewards_per_episode

In [10]:
if __name__ == "__main__":
    average, scores = run_ttt_n_games_and_return_mean_score(1000)

  0%|                                                                                         | 0/1000 [00:00<?, ?it/s]

Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récomp

Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise réc

Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne 

Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne 

...

Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une 

Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
U

  0%|                                                                                         | 0/1000 [01:43<?, ?it/s]


Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une bonne récompense
Une mauvaise récompense
Une mauvaise récompense
Une bonne récompense
Une bonne récompense
Une

KeyboardInterrupt: 